
File: 08-lecture.py


Michel Bierlaire

Fri Aug 23 18:32:16 2024




In [ ]:

import itertools
import pandas as pd
from IPython.core.display_functions import display
import biogeme.biogeme_logging as blog
from biogeme.biogeme import BIOGEME
from biogeme.expressions import Beta, log, exp, Expression
from biogeme.models import loglogit, logit
from biogeme.results import compile_estimation_results, bioResults
from pandas import Series


Variables used for the specification of the Swissmetro model are defined in the file `swissmetro_variables.py`.

In [ ]:
from swissmetro_variables import (
    database,
    CHOICE,
    TRAIN_AV_SP,
    SM_AV,
    CAR_AV_SP,
    TRAIN_TT_SCALED,
    TRAIN_COST_SCALED,
    TRAIN_HE_SCALED,
    SM_TT_SCALED,
    SM_COST_SCALED,
    SM_HE_SCALED,
    CAR_TT_SCALED,
    CAR_CO_SCALED,
    MALE,
    GA,
    BUSINESS,
    LOW_INC,
    FIRST,
)


As the estimation time may be long, we ask Biogeme to report the details of the iterations.

In [ ]:
logger = blog.get_screen_logger(level=blog.INFO)


The objective of this series of exercises is to perform a similar modeling exercise as seen during the lecture.

# Parameters

In [ ]:
asc_car = Beta('asc_car', 0, None, None, 0)
asc_train = Beta('asc_train', 0, None, None, 0)
b_time = Beta('b_time', 0, None, None, 0)
b_cost = Beta('b_cost', 0, None, None, 0)
b_fr = Beta('b_fr', 0, None, None, 0)



# Availability conditions

In [ ]:
av = {1: TRAIN_AV_SP, 2: SM_AV, 3: CAR_AV_SP}



# Logit model

## Utility functions

In [ ]:
V1 = (
    asc_train
    + b_time * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V = {1: V1, 2: V2, 3: V3}



## Model

In [ ]:
logprob = loglogit(V, av, CHOICE)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob)
biogeme.modelName = '01logit'
results_logit = biogeme.estimate(recycle=True)



## Results

General statistics

In [ ]:
print(results_logit.print_general_statistics())


Estimated parameters

In [ ]:
param_logit = results_logit.get_estimated_parameters()
display(param_logit)


The starting point is the logit model presented above.

1. Load the results of the model where the travel time coefficient is normally distributed within the population.

2. Load the results of the model where the travel time coefficient is log normally distributed within the population.

3. Load the results of the model with two latent classes: one where the travel time coefficient is constrained to
be zero, and one where the travel time coefficient is estimated.

4. Estimate the same latent class model, including a class membership model, that involves the following binary
variables:

- `MALE`: 1 if individual is male.

- `GA`: 1 if individual owns a yearly subscription.

- `PURPOSE == 3`: 1 if trip purpose is business.

- `INCOME <= 1`: 1 if the income is less or equal to 50kCHF per year.

- `FIRST`: 1 if the individual is a first class traveler.

5. Calculate, for each segment of the population, the probability to be in each class.

6. Compare the results